# ConceptNetist lisaküsimuste saamine

In [ ]:
# tõlgime sõna inglise keelde
# leiame seosed ConceptNetist
# tõlgime seosed eesti keelde
# teeme erinevatest seoste tüüpidest küsimused
# ühendame sõna ja küsimuse
# lisame juurde alamsõnede seosed

## importimine

In [ ]:
from google.colab import drive

drive.mount('/content/drive')

import os
os.chdir('/content/drive/My Drive/Colab Notebooks/baka')

Mounted at /content/drive


In [ ]:
!pip install requests

In [ ]:
!pip install estnltk==1.7.3
import estnltk
from estnltk import Text

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 70.8/70.8 MB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.8/235.8 kB 9.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 18.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.3/118.3 kB 9.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 39.8 MB/s eta 0:00:00


In [ ]:
import nltk
nltk.download('punkt_tab')

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


True

In [ ]:
import pandas as pd

## andmete failist lugemine

In [ ]:
df = pd.read_csv('mängu_andmed_loomad.csv')

In [ ]:
words = df["Loom"].tolist() #len = 1280

## Sõnade tõlkimise funktsioon

In [ ]:
import requests

# https://translate.ut.ee/API
# https://github.com/TartuNLP/translation-api

import time

session = requests.Session()

def translate_text(text, src, tgt, url="https://api.tartunlp.ai/translation/v2"):
    headers = {
        "x-api-key": "public",
        "Content-Type": "application/json"
    }
    data = {
        "text": text,
        "src": src,
        "tgt": tgt,
        "application": "test-application"
    }

    try:
        response = session.post(url, json=data, headers=headers)
        response.raise_for_status()  # Raise error for bad responses
        return response.json().get("result")
    except requests.exceptions.RequestException as e:
        print(f"Translation error: {e}")
        return None



In [ ]:
from estnltk.vabamorf.morf import synthesize
def correct_word_form(word, vabamorf):
  word = word.split(".")
  word = word[0]
  sõna = ""
  for w in word.split():
    synthesized = synthesize(w, vabamorf)
    if synthesized:
        sõna += synthesized[0] + " "
    else:
        return

  if sõna == "":
    return word
  return sõna.strip()

## Küsimuste genereerimine

In [ ]:
def generate_question(words, relation):
  verb = ""
  noun = ""

  words = translate_text(words, "en", "et")
  text = Text(words).tag_layer().morph_analysis

  if relation == "CapableOf": # kasutan sõnapaare mis on kujul VERB + NOUN
    for i in range(len(text.lemma)):
      wordPOS = text.partofspeech[i]
      if wordPOS[0] == 'V':
        if correct_word_form(text.lemma[i][0], "b"):
          verb = correct_word_form(text.lemma[i][0], "b")
        else:
          verb = text.lemma[i][0]
      elif wordPOS[0] == "S":
        noun = correct_word_form(text.lemma[i][0], "pl p")
      else:
        continue
    if not noun or not verb:
      return
    else:
      question = f"Kas see loom {verb} {noun}?"
  elif relation == "AtLocation": # kasutan ainult ühte NOUNi
    for i in range(len(text.lemma)):
      wordPOS = text.partofspeech[i]
      if wordPOS[0] == "S":
        noun = correct_word_form(text.lemma[i][0], "sg ad")
      else:
        continue
    if not noun:
      return
    else:
      question = f"Kas seda looma võib leiduda {noun}?"

  return translate_text(question, "et", "et")

## Seoste saamine ConceptNetist

In [ ]:
import requests
import time

# Create a session for efficiency
session = requests.Session()
session.headers.update({"Connection": "keep-alive"})  # Keep the session alive

def get_conceptnet_relationships(word):
    base_url = "http://api.conceptnet.io"
    start_url = f"/query?node=/c/en/{word}"
    min_weight = 0.9  # Set minimum weight threshold
    target_relations = {"CapableOf", "AtLocation"}
    filtered_edges = []
    questions = set()

    # Loop through pages
    while start_url:
        try:
            response = session.get(base_url + start_url, timeout=10)  # Use session for better performance
            response.raise_for_status()  # Ensure successful request
            data = response.json()

            for edge in data.get("edges", []):
                relation = edge["rel"]["label"]
                weight = edge.get("weight", 0)

                if relation in target_relations and weight > min_weight:
                    filtered_edges.append(edge)

            start_url = data.get("view", {}).get("nextPage")  # Get next page URL

            time.sleep(0.5)  # Small delay to avoid rate limiting

        except requests.exceptions.RequestException as e:
            print(f"Error fetching data for {word}: {e}")
            break  # Stop on error

    # Sort edges by weight in descending order and select the top 30
    filtered_edges = sorted(filtered_edges, key=lambda x: x.get("weight", 0), reverse=True)[:35]

    # Collect filtered relationships
    for edge in filtered_edges:
        relation = edge["rel"]["label"]
        target = edge["end"]["label"]
        if all(part != word for part in target.split()):
            question = generate_question(target, relation)
            questions.add(question)

    return questions


## main run ja faili kirjutamine

In [ ]:
#word_questions = {}
#for word in words:
#  wordENG = translate_text(word, "et", "en")
#  word_questions[word] = get_conceptnet_relationships(wordENG)

In [ ]:
import json

# Remove None values and convert sets to lists
#word_questions = {word: list({q for q in questions if q is not None}) for word, questions in word_questions.items()}

# Save to file
#with open("word_questions.txt", "w", encoding="utf-8") as file:
#    json.dump(word_questions, file, ensure_ascii=False, indent=4)

## loeme failid sisse ja leiame alammõisted

In [ ]:
hyponyms_data

'[[\'ammonoteel\', \'ammonoteelid\'], set()]\n[[\'koprofaag\', \'roojasööja\'], set()]\n[[\'kasur\'], set()]\n[[\'hematofaag\'], set()]\n[[\'geofaag\'], set()]\n[[\'fossoor\'], set()]\n[[\'desertikool\', \'kõrbeloom\'], set()]\n[[\'biofiltraator\', \'biofiltraatorid\', \'filtraator\', \'filtreerija\', \'filtrija\'], set()]\n[[\'villaloom\'], set()]\n[[\'põhjaveeorganism\', \'stügobiont\'], set()]\n[[\'püsisoojane\', \'püsisoojane loom\'], set()]\n[[\'kõigusoojane\', \'kõigusoojane loom\'], set()]\n[[\'elajas\'], set()]\n[[\'montikool\', \'mäestikuloom\'], set()]\n[[\'petrikool\'], set()]\n[[\'arbolikool\', \'dendrobiont\'], set()]\n[[\'keratofaag\'], set()]\n[[\'psammofiil\'], {\'arenikool\'}]\n[[\'arenikool\'], set()]\n[[\'kandeloom\'], set()]\n[[\'maismaaloom\'], set()]\n[[\'bentofaag\'], set()]\n[[\'destsendent\', \'järeltulija\', \'järglane\', \'pojad\'], {\'loomahakatis\', \'härgvasikas\', \'eluvasikas\', \'piimavasikas\', \'vasikas\', \'angerjamaim\', \'koerahakatis\', \'linnuhak

In [ ]:
import ast

hyponym_map = {}  # Dictionary to store results

with open("word_hyponyms.txt", "r", encoding="utf-8") as file:
    for line in file:
        line = line.strip()
        line = line.replace("set()", "[]")  # Replace `set()` with `[]` for eval
        print(line)
        my_list = ast.literal_eval(line)  # Convert string to list

        key = tuple(my_list[0])  # Convert list to a tuple (hashable)
        hyponym_map[key] = my_list[1]  # Assign the second element

print(hyponym_map)



[['ammonoteel', 'ammonoteelid'], []]
[['koprofaag', 'roojasööja'], []]
[['kasur'], []]
[['hematofaag'], []]
[['geofaag'], []]
[['fossoor'], []]
[['desertikool', 'kõrbeloom'], []]
[['biofiltraator', 'biofiltraatorid', 'filtraator', 'filtreerija', 'filtrija'], []]
[['villaloom'], []]
[['põhjaveeorganism', 'stügobiont'], []]
[['püsisoojane', 'püsisoojane loom'], []]
[['kõigusoojane', 'kõigusoojane loom'], []]
[['elajas'], []]
[['montikool', 'mäestikuloom'], []]
[['petrikool'], []]
[['arbolikool', 'dendrobiont'], []]
[['keratofaag'], []]
[['psammofiil'], {'arenikool'}]
[['arenikool'], []]
[['kandeloom'], []]
[['maismaaloom'], []]
[['bentofaag'], []]
[['destsendent', 'järeltulija', 'järglane', 'pojad'], {'loomahakatis', 'härgvasikas', 'eluvasikas', 'piimavasikas', 'vasikas', 'angerjamaim', 'koerahakatis', 'linnuhakatis', 'kassipoeg', 'naisjäreltulija', 'lehmik', 'kalamaim', 'ristsugutis', 'karupoeg'}]
[['naisjäreltulija'], []]
[['ristsugutis'], []]
[['linnuhakatis', 'linnupoeg'], []]
[['loo

In [ ]:
with open("word_questions.txt", "r", encoding="utf-8") as file:
    questions_data = json.loads(file.read())

In [ ]:
questions_data

{'ameerika paalia': [],
 'arvicola terrestris': [],
 'campbelli käpikhamstrik': [],
 'Dalli lammas': [],
 'Jack Russel': [],
 'kalifornia pringel': [],
 'aafrika elevant': [],
 'aafrika pühvel': [],
 'aafrika tsiibet': [],
 'aaga': [],
 'aara': [],
 'aasia lõvi': [],
 'aasia taapir': [],
 'abakala': [],
 'aberdiin': [],
 'abikoer': [],
 'addaks': [],
 'aed-lepalind': [],
 'aed-põõsalind': [],
 'afaliin': [],
 'afgaani hurt': [],
 'afgaani rebane': [],
 'aguuti': [],
 'aguutilane': [],
 'käblik': [],
 'ahv': ['Kas seda looma võib tsirkuses leiduda?',
  'Kas see loom võib olla džunglipiirkonnas?',
  'Kas see loom sööb banaane?',
  'Kas seda looma võib loomaaias leiduda?',
  'Kas see loom võib olla filmis?',
  'Kas seda looma võib metsas leiduda?',
  'Kas see loom võib olla vihmametsas?',
  'Kas seda looma võib teaduslaboris leiduda?'],
 'ahven': [],
 'aisahobune': [],
 'ajukoer': [],
 'albatross': ['Kas see loom maandub pinnale?'],
 'laiksilm-delfiin': [],
 'alk': [],
 'allosaurus': [],


In [ ]:
# vaatame paljud küsimused korduvad
unique_questions = set()
all_questions = []
duplicates = 0
example = ""

for words, questions in questions_data.items():
    all_questions.extend(questions)  # Add all questions to the list
    for question in questions:
        if question in unique_questions:
            duplicates += 1  # Count duplicates
            example += question
        else:
            unique_questions.add(question)  # Add to unique set

# Print the number of unique and duplicate questions
print(f"Unique questions: {len(unique_questions)}")
print(f"Total questions: {len(all_questions)}")
print(f"Duplicate questions: {duplicates}")
#print(example)

Unique questions: 164
Total questions: 276
Duplicate questions: 112
Kas seda looma on vees?Kas seda looma võib tsirkuses leiduda?Kas seda looma võib loomaaias leiduda?Kas seda looma võib loomaaias leiduda?Kas seda looma võib ookeanis leiduda?Kas see loom võib olla pööningul?Kas see loom võib olla viljaprügilas?Kas see loom võib keldris olla?Kas seda looma võib poest leida?Kas see loom võib olla seinas?Kas see loom kardab kasse?Kas seda looma võib aias leiduda?Kas seda looma võib kodus leiduda?Kas seda looma võib kanalisatsioonis leiduda?Kas seda looma võib kassil leiduda?Kas seda looma võib köögis leiduda?Kas seda looma võib laboris leiduda?Kas seda looma võib tsirkuses leiduda?Kas seda looma võib metsas leiduda?Kas seda looma võib leiduda meres?Kas seda looma võib loomaaias leiduda?Kas seda looma võib loomaaias leiduda?Kas seda looma võib ookeanis leiduda?Kas seda looma võib akvaariumis leiduda?Kas see loom muneb mune?Kas see loom joob vett?Kas seda looma võib kodus leiduda?Kas see lo

In [ ]:
# käin läbi kõik df["Loom"] väljad ja vaatan, kas antud loomale on mõni küsimus juurde lisada
# kui on kontrollin, et sellist küsimust juba ei ole
# kui küsimust juba ei ole, lisan selle küsimuse df ja lisan loomale seoseks 1 ja kõigile alammõistetele ka 1, muidu 0
# kui küsimus on juba olemas, siis lisan seosed, mida veel ei ole

# Funktsioon küsimuste lisamiseks
def update_questions(df, questions_data, hyponym_map):
    for word, questions in questions_data.items():
        if questions:  # Ensures questions is not empty
            updated_words = set()

            # Find main words and hyponyms
            for mainword, hyponyms in hyponym_map.items():
                if word in mainword:
                    updated_words.add(word)
                    updated_words.update(hyponyms)

            # Process each updated word
            for question in questions:
                if question not in df.columns:
                    df[question] = 0  # Create a new column if it doesn't exist

                # Update the values: set 1 for matching "Loom" values
                df.loc[df["Loom"].isin(updated_words) & df[question].isna(), question] = 1

    return df

# Rakendame funktsiooni
updated_df = update_questions(df, questions_data, hyponym_map)



In [ ]:
updated_df

Loom  Unnamed: 1  \
0                ameerika paalia           1   
1            arvicola terrestris           0   
2        campbelli käpikhamstrik           0   
3                   Dalli lammas           0   
4                    Jack Russel           1   
5             kalifornia pringel           0   
6                aafrika elevant           0   
7                 aafrika pühvel           0   
8                aafrika tsiibet           0   
9                           aaga           0   
10                          aara           1   
11                    aasia lõvi           0   
12                  aasia taapir           0   
13                       abakala           1   
14                      aberdiin           1   
15                       abikoer           1   
16                        addaks           1   
17                  aed-lepalind           1   
18                 aed-põõsalind           1   
19                       afaliin           0   
20                  afgaani hurt           1   
21                afgaani rebane           0   
22                        aguuti           0   
23                    aguutilane           0   
24                        käblik           1   
25                           ahv           0   
26                         ahven           1   
27                    aisahobune           1   
28                       ajukoer           1   
29                     albatross           1   
30              laiksilm-delfiin           0   
31                           alk           1   
32                    allosaurus           0   
33                 ameerika curl           1   
34                ameerika jänes           0   
35                       ammlehm           1   
36                        ammuja           1   
37                 amuuri tiiger           0   
38                      anakonda           0   
39                      angerjas           1   
40                     angersäga           1   
41                   angvantiibo           0   
42                          anoa           0   
43                      antiloop           0   
44                     antropoid           0   
45                       anuubis           0   
46                        apella           0   
47                      ararauna           1   
48                ardenni hobune           1   
49                        arhaar           0   
50                      argamakk           1   
51                  arheopterüks           1   
52                      armadill           0   
53                          arni           0   
54                        asiiti           1   
55                      astelrai           1   
56                 atlandi tursk           1   
57                           aul           1   
58                    australorp           1   
59               avamaastikulind           1   
60                 avaspesitseja           1   
61                       babuiin           0   
62                        baibak           0   
63       baieri ulukijälituskoer           1   
64                baikali viiger           0   
65                   bali tiiger           0   
66                    bambuskaru           0   
67                       banteng           0   
68                       baribal           0   
69                        barsoi           1   
70                        basset           1   
71                        beagle           1   
72                         beira           0   
73                bengali tiiger           0   
74                    berberiahv           0   
75                   bernhardiin           1   
76                   besoaarkits           0   
77                       biruang           0   
78                       bitjuug           0   
79                           boa           0   
80                        bokser           1   
81             boliivia anakonda           0   
82                         bongo           0

In [ ]:

updated_df = updated_df.drop(columns=["Unnamed: 1"])

In [ ]:
updated_df = updated_df.drop(columns=["Kas see loom on ?"])


In [ ]:
updated_df

Loom  Kas seda looma võib leiduda avamaastikus?  \
0                ameerika paalia                                          0   
1            arvicola terrestris                                          0   
2        campbelli käpikhamstrik                                          0   
3                   Dalli lammas                                          0   
4                    Jack Russel                                          0   
5             kalifornia pringel                                          0   
6                aafrika elevant                                          0   
7                 aafrika pühvel                                          0   
8                aafrika tsiibet                                          0   
9                           aaga                                          0   
10                          aara                                          0   
11                    aasia lõvi                                          0   
12                  aasia taapir                                          0   
13                       abakala                                          0   
14                      aberdiin                                          0   
15                       abikoer                                          0   
16                        addaks                                          0   
17                  aed-lepalind                                          0   
18                 aed-põõsalind                                          0   
19                       afaliin                                          0   
20                  afgaani hurt                                          0   
21                afgaani rebane                                          0   
22                        aguuti                                          0   
23                    aguutilane                                          0   
24                        käblik                                          0   
25                           ahv                                          0   
26                         ahven                                          0   
27                    aisahobune                                          0   
28                       ajukoer                                          0   
29                     albatross                                          0   
30              laiksilm-delfiin                                          0   
31                           alk                                          0   
32                    allosaurus                                          0   
33                 ameerika curl                                          0   
34                ameerika jänes                                          0   
35                       ammlehm                                          0   
36                        ammuja                                          0   
37                 amuuri tiiger                                          0   
38                      anakonda                                          0   
39                      angerjas                                          0   
40                     angersäga                                          0   
41                   angvantiibo                                          0   
42                          anoa                                          0   
43                      antiloop                                          0   
44                     antropoid                                          0   
45                       anuubis                                          0   
46                        apella                                          0   
47                      ararauna                                          0   
48                ardenni hobune                                          0   
49                        arhaar                                          0   

In [ ]:
updated_df.to_csv('game_data_animals_final.csv', index=False)

In [ ]:
#viimased katsetused

In [ ]:
df = pd.read_csv('game_data_animals_final.csv')

In [ ]:
df = df.rename(columns={"Loom": "Sõna"})

In [ ]:
for col in df.columns: # veerud: Synonyms, tähtsus
    print(col)

Sõna
Kas seda looma võib leiduda avamaastikus?
Kas seda looma võib leiduda avameres?
Kas seda looma võib leiduda avaspesas?
Kas seda looma võib leiduda järves?
Kas seda looma võib leiduda jões?
Kas seda looma võib leiduda lähistroopikas?
Kas seda looma võib leiduda mererannikus?
Kas seda looma võib leiduda tiigis?
Kas see loom ammub?
Kas see loom haub?
Kas see loom hirnahtab?
Kas see loom hirnub?
Kas see loom imetab?
Kas see loom kireb?
Kas see loom korskab?
Kas see loom krooksub?
Kas see loom kädistab?
Kas see loom lauldes häälitseb?
Kas see loom liristab?
Kas see loom lüpsab?
Kas see loom mäugub?
Kas see loom määgib?
Kas see loom nuriseb?
Kas see loom on 16–22 cm pikkune, tiibade siruulatus on 35–40 cm?
Kas see loom on 18–20 cm pikk, soorüdist veidi suurem lühikese noka ja kollaste jalgadega kahlaja, välimuse poolest tutka sarnane?
Kas see loom on Aafrika hõrendikel, savannides ja põõsastega tasandikel elutsev kabriklane?
Kas see loom on Aafrika ja Aasia mõneti kärpi meenutav kiskjal

In [ ]:
df.to_csv('game_data_animals_final.csv', index=False)

In [ ]:
question = "Kas see loom võib roomajal olla?"
df[df[question] == 1]

Sõna  Kas seda looma võib leiduda avamaastikus?  \
32              allosaurus                                          0   
84           brahhiosaurus                                          0   
88            brontosaurus                                          0   
103             dinosaurus                                          0   
104            diplodookus                                          0   
108           dromeosaurus                                          0   
152          gigantosaurus                                          0   
156            gorgosaurus                                          0   
214           hiid-ogasaba                                          0   
278             iguaanodon                                          0   
312   jaanalind-dinosaurus                                          0   
393     karharodontosaurus                                          0   
747                ogasaba                                          0   
778           pareiasaurus                                          0   
812           plesiosaurus                                          0   
829           prosauropood                                          0   
835            pterosaurus                                          0   
961              sauropood                                          0   
964           seismosaurus                                          0   
990                sisalik                                          0   
1008           stegosaurus                                          0   
1072           teleosaurus                                          0   
1074              teropood                                          0   
1075              tetanuur                                          0   
1097         tritseeratops                                          0   
1100         tseratosaurus                                          0   
1149         türannosaurus                                          0   

      Kas seda looma võib leiduda avameres?  \
32                                        0   
84                                        0   
88                                        0   
103                                       0   
104                                       0   
108                                       0   
152                                       0   
156                                       0   
214                                       0   
278                                       0   
312                                       0   
393                                       0   
747                                       0   
778                                       0   
812                                       0   
829                                       0   
835                                       0   
961                                       0   
964                                       0   
990                                       0   
1008                                      0   
1072                                      0   
1074                                      0   
1075                                      0   
1097                                      0   
1100                                      0   
1149                                      0   

      Kas seda looma võib leiduda avaspesas?  \
32                                         0   
84                                         0   
88                                         0   
103                                        0   
104                                        0   
108                                        0   
152                                        0   
156                                        0   
214                                        0   
278                                        0   
312                                        0   
393                                        0   
747                                 

In [ ]:
row = df[df["Sõna"] == "koer"]  # Leia rida, kus "Sõna" on "kana"

if not row.empty:  # Kontrollime, et rida on leitud
    yes_columns = row.iloc[0][row.iloc[0] == 1].index.tolist()  # Leia veerud, kus väärtus on 1
    print("Jaatavalt vastatud küsimuste veerud:", yes_columns)
else:
    print("Viga: Sõna 'kana' ei leitud andmestikust.")

for col in yes_columns: # veerud: Synonyms, tähtsus
    print(col)


Jaatavalt vastatud küsimuste veerud: ['Kas see loom on peamiselt hundist põlvnev koduloom?', 'Kas tegu on imetajaga?', 'Kas tegu on kodukoeraga?', 'Kas tegu on koduloomaga?', 'Kas tegu on koerlasega?', 'Kas tegu on loomaga?', 'Kas tegu on neljajalgsega?', 'Kas tegu on selgroogsega?', 'tähtsus', 'Kas see loom märgistab territooriume?', 'Kas see loom joob vett?', 'Kas see loom on lemmikloom?', 'Kas see loom võib olla tagahoovis?', 'Kas see loom võib voodis olla?', 'Kas seda looma võib majas leiduda?', 'Kas see loom valvab majasid?', 'Kas see loom kaevab luid?', 'Kas see loom võib olla kuudis?', 'Kas see loom juhendab pimedaid inimesi?', 'Kas see loom kuuleb vilistamist?', 'Kas see loom teeb trikke?', 'Kas see loom võib kennelis olla?', 'Kas seda looma võib pargis leiduda?', 'Kas see loom võitleb kassidega?']
Kas see loom on peamiselt hundist põlvnev koduloom?
Kas tegu on imetajaga?
Kas tegu on kodukoeraga?
Kas tegu on koduloomaga?
Kas tegu on koerlasega?
Kas tegu on loomaga?
Kas tegu on 

In [ ]:
row = df[df["Sõna"] == "mops"]  # Leia rida, kus "Sõna" on "kana"

if not row.empty:  # Kontrollime, et rida on leitud
    yes_columns = row.iloc[0][row.iloc[0] == 1].index.tolist()  # Leia veerud, kus väärtus on 1
    print("Jaatavalt vastatud küsimuste veerud:", yes_columns)
else:
    print("Viga: Sõna 'kana' ei leitud andmestikust.")

for col in yes_columns: # veerud: Synonyms, tähtsus
    print(col)

Jaatavalt vastatud küsimuste veerud: ['Kas see loom on väike tömbi nina ja rõngas sabaga toakoer.?', 'Kas tegu on imetajaga?', 'Kas tegu on kodukoeraga?', 'Kas tegu on koduloomaga?', 'Kas tegu on koerlasega?', 'Kas tegu on loomaga?', 'Kas tegu on neljajalgsega?', 'Kas tegu on selgroogsega?', 'Kas tegu on toakoeraga?', 'Kas see loom märgistab territooriume?', 'Kas see loom joob vett?', 'Kas see loom on lemmikloom?', 'Kas see loom võib olla tagahoovis?', 'Kas see loom võib voodis olla?', 'Kas seda looma võib majas leiduda?', 'Kas see loom valvab majasid?', 'Kas see loom kaevab luid?', 'Kas see loom võib olla kuudis?', 'Kas see loom juhendab pimedaid inimesi?', 'Kas see loom kuuleb vilistamist?', 'Kas see loom teeb trikke?', 'Kas see loom võib kennelis olla?', 'Kas seda looma võib pargis leiduda?', 'Kas see loom võitleb kassidega?']
Kas see loom on väike tömbi nina ja rõngas sabaga toakoer.?
Kas tegu on imetajaga?
Kas tegu on kodukoeraga?
Kas tegu on koduloomaga?
Kas tegu on koerlasega?
K